#  Classificação a partir de conjuntos de treinamento gerados para QP3LOT

In [1]:
# import warnings
# warnings.filterwarnings('ignore')  # "error", "ignore", "always", "default", "module" or "once"
import numpy as np
import math
import pandas as pd
import matplotlib
%matplotlib inline
import sys
import os
import glob
import re

# janelas = [1, 0.01, 0.03, 0.05] # K = {1, 1%, 3%, 5%}
abordagens = ["dgArj", "ptChr"] #Quando houver a janela vencedora. Após testar as combinações acima
                 #com todas as bases. Lembrando que só deve ser usada para as demais QP além e QP6

# janelas = [100] #Quando for utilizar Peter Christen. Ou então, criar um conjunto de 3 valores
                    # de modo que cada um represente DgArj, PtChr ou Aleatório

# bases = ["cds", "cds1", "cds2"]
bases = ["cd"]
# qps = ["QP1", "QP2"] #Todos menos QP6
# qps = ["qp1", "qp2b", "qp2m", "qp2r", "qp3all", "qp3lot"] #Todos menos QP6 e QP7
# qps = ["qp1", "qp2b", "qp2r", "qp3all", "qp3lot"] #Todos menos QP6 e QP7 - (Considerando 2 grupos divididos pela mediaa)
qps = ["qp3lot"] #Todos menos QP6 e QP7 - (Considerando 2 grupos divididos pela mediaa)
regiao = "incert"
janela = 0.01


for base in bases:
    
    print("Base atual: {0}".format(base))
    
    for qp in qps: #Loop abrangendo os dois classificadores
        
        print("QP atual: {0}".format(qp))
    
        for k in abordagens: 

            abordagemAA = ""
            
            dirOrig = ""
            dirEstat = ""
            estat = ""
            
            if(k == "ptChr"): #Se Peter Christen
                
                abordagemAA = '2 - AA[pet-chr]'
            
                dirOrig = "../csv/conjuntosDS/treinoTeste/"+base+"/"+qp+"/"+"PtChr/"
                dirEstat = "../csv/estatisticas/"+base+"/"+qp+"/"
                estat = dirEstat+"estatisticaDS2-PtChr.csv"
    #   
            elif(k == "dgArj"): #Se Diego Araújo
            
                abordagemAA = '2 - AA[dg-arj]'
            
#                 dirOrig = "../csv/conjuntosDS/treinoTeste/"+base+"/"+qp+"/"+"DgArj/"
                dirOrig = "../csv/conjuntosDS/treinoTeste/"+base+"/"+qp+"/"+"DgArj-k"+str(janela)+"/"
                dirEstat = "../csv/estatisticas/"+base+"/"+qp+"/"
                #                 estat = dirEstat+"estatisticaDS2-DgArj.csv"
                estat = dirEstat+"estatisticaDS2-DgArj-k"+str(janela)+".csv"
                
            elif(k == "rand"): #Se Random
            
                abordagemAA = '2 - AA[random]'
            
                dirOrig = "../csv/conjuntosDS/treinoTeste/"+base+"/"+qp+"/"+"Random/"
                dirEstat = "../csv/estatisticas/"+base+"/"+qp+"/"
                estat = dirEstat+"estatisticaDS2-Random.csv"
                
            print("**************************")
            print("Base: {0} - {1} - Abordagem: {2} - Classificador: rf".format(base,qp,abordagemAA))
            print("**************************")
            
            print(dirOrig)

            etapa = '3 - clasf'

            # estatisticas = pd.read_csv(estat, index_col=['etapa','permutacao'], sep=';')
            estatisticas = pd.read_csv(estat, index_col=['algoritmosUtilizados','permutacao','etapa'], sep=';')
        #     estatisticas.tail()

            arquivos = os.listdir(dirOrig)
            # print(arquivos)
            #print(len(arquivos))

            train = []
            test = []

            for arq in arquivos:
                if arq.startswith("train"):
                    train.append(arq)
                elif arq.startswith("test"):
                    test.append(arq)

            # print('tamanho de train: %d' %(len(train)))        

            # print('tamanho de test: %d' %(len(test)))

            # print (train)    
            # print (test)    

            lista =[]

            #lista = ['10', '15', '20', '25'] #Assumindo que serão esses os conjuntos de algoritmos
            #ATENÇÃO, DIEGO!! ISSO MUDA PARA QP2 E QP3
            if (qp == "qp1"):
                lista = ['5', '15', '25'] #Assumindo que serão esses os conjuntos de algoritmos 
            elif (qp == "qp2b"):
                lista = ['8'] #Assumindo que serão esses os conjuntos de algoritmos 
            elif (qp == "qp2m"):
                lista = ['8'] #Assumindo que serão esses os conjuntos de algoritmos 
            elif (qp == "qp2r"):
                lista = ['8'] #Assumindo que serão esses os conjuntos de algoritmos 
            elif (qp == "qp3all"):
                lista = ['13'] #Assumindo que serão esses os conjuntos de algoritmos 
            elif (qp == "qp3lot"):
                lista = ['5'] #Assumindo que serão esses os conjuntos de algoritmos 
            
            for i in lista: 

                cont = 0

                trainAtual = []
                testAtual = []

                for arq in train:
                    if '('+i+')' in arq:
        #             if 'train(10)22' in arq:    
                        trainAtual.append(arq)
                for arq in test:
                    if '('+i+')' in arq:
        #             if 'test(10)22' in arq:
                        testAtual.append(arq)

            #     print('lista desordenada')
            #     print(trainAtual)

            #     print('tamanho antes: %d' %(len(trainAtual)))

                #Ordenando a lista
                trainAtual = sorted(trainAtual)
                testAtual = sorted(testAtual)

            #     for x in trainAtual:
            #         print(x)



            # #     print('lista ordenada')
            # #     print(trainAtual)

            #     print('tamanho depois: %d' %(len(trainAtual)))

            #     print(type(trainAtual))


                print (i)

            #     print(trainAtual)
            #     print(testAtual)

                tam = len(trainAtual) #Mesma coisa para testAtual

                for pos in range(tam):
            #         print(pos)
                    print('')
                    print('##########################')
                    print('Arquivos atuais: %s e %s' %(trainAtual[pos], testAtual[pos]))
                    print('##########################')

                    treino = dirOrig+trainAtual[pos]
                    teste = dirOrig+testAtual[pos]

            #         print('treino: %s' %(treino))

            #         tp, fp, tn, fn = 0

                    num = trainAtual[pos].replace('train('+i+')','')
                    num = num.replace('.csv','')

                    cont += 1

                    print('Iteração: %d' %(cont))

            #         print('num: %s' %(num))

                    algUtl = re.sub('train.*\(', r'', trainAtual[pos]) #Alterar para fazer a substituição de tudo em uma linha só
                    algUtl = re.sub('\).*', r'', algUtl) #Alterar para fazer a substituição de tudo em uma linha só
                    algUtl = int(algUtl)


                    print('algUtl: %d' %(algUtl))

                    permutacao = int(num)
            #         linhaAtual = estatisticas.loc[('2 - AA[pet-chr]', permutacao), : ] #Armazena a linha correspondente à permutação
            #         linhaAtual = estatisticas.loc[('1 - acm diverg', permutacao), : ] #Armazena a linha correspondente à permutação
                    linhaAtual = estatisticas.loc[algUtl, permutacao, abordagemAA, : ] #Armazena a linha correspondente à permutação
        #             print (linhaAtual)
        #             print(linhaAtual.columns)

                #'''
            #         all = pd.read_csv("train.csv", index_col=False, sep=';', names=('title', 'artist', 'track01', 'track02', 'track03', 'duplicata'), header = None)
            #         toClass = pd.read_csv("test.csv", index_col=False, sep=';', names=('title', 'artist', 'track01', 'track02', 'track03', 'duplicata'), header = None)

            #         all = pd.read_csv(treino, index_col=False, sep=';', names=('title', 'artist', 'track01', 'track02', 'track03', 'duplicata'), header = None)
            #         toClass = pd.read_csv(teste, index_col=False, sep=';', names=('title', 'artist', 'track01', 'track02', 'track03', 'duplicata'), header = None)

                    all = pd.read_csv(treino, index_col=False, sep=';', names=('title', 'artist', 'track01', 'track02', 'track03', 'track10', 'track11', 'duplicata'), header = 0) #Era header = None
                    toClass = pd.read_csv(teste, index_col=False, sep=';', names=('title', 'artist', 'track01', 'track02', 'track03', 'track10', 'track11', 'duplicata'), header = 0) #Era header = None


                    # all['artist-title'] = all['artist'] * all['title']
                    # cols = list(all.columns.values)
                    # cols.pop(cols.index('duplicata'))
                    # all = all[cols+['duplicata']]

                    #Pesos baseados no Alg17

                    all['artist-title'] = all['artist'] * all['title']
                    all['soma-pesos'] = (all['artist']*1 + all['title']*2 + all['track01']*0.8 + all['track02']*0.8)/4.6
                    cols = list(all.columns.values)
                    cols.pop(cols.index('duplicata'))
                    all = all[cols+['duplicata']]

                    # toClass['artist-title'] = toClass['artist'] * toClass['title']
                    # cols = list(toClass.columns.values)
                    # cols.pop(cols.index('duplicata'))
                    # toClass = toClass[cols+['duplicata']]

                    #Pesos baseados no Alg17

                    toClass['artist-title'] = toClass['artist'] * toClass['title']
                    toClass['soma-pesos'] = (toClass['artist']*1 + toClass['title']*2 + toClass['track01']*0.8 + toClass['track02']*0.8)/4.6
                    cols = list(toClass.columns.values)
                    cols.pop(cols.index('duplicata'))
                    toClass = toClass[cols+['duplicata']]

                    #Separação do conjunto X do conjunto y
                    # X = all.loc[:,'title':'artist-title']
                    X = all.loc[:,'title':'soma-pesos']
                    y = all.duplicata

                    # XtoClass = toClass.loc[:,'title':'artist-title']
                    XtoClass = toClass.loc[:,'title':'soma-pesos']
                    ytoClass = toClass.duplicata

                    from sklearn import model_selection

                    X_train, X_test, y_train, y_test = model_selection.train_test_split(X, y, test_size=0.20, random_state=2)

                    from sklearn.ensemble import RandomForestClassifier
                    from sklearn.model_selection import StratifiedKFold
                    from sklearn.model_selection import KFold
                    from sklearn import model_selection

                    seed = 500

                    '''

                    from sklearn.linear_model import LogisticRegression
                    from sklearn.tree import DecisionTreeClassifier
                    from sklearn.neighbors import SVC
                    from sklearn.svm import SVC

                    modelos = []
                    modelos.append(('LR', LogisticRegression()))
                    modelos.append(('KNN', SVC()))
                    modelos.append(('RFC', DecisionTreeClassifier()))
                    modelos.append(('SVM', SVC()))
                    modelos.append(('RF', RandomForestClassifier()))



                    # Avaliação de cada modelo por vez
                    resultados = []
                    nomes = []
                    for nome, modelo in modelos:
                        kfold = StratifiedKFold(n_splits=10, random_state=seed) #Mudar para n-fold
                        cv_results = model_selection.cross_val_score(modelo, X_train, y_train, cv=kfold, scoring='f1')
                        msg = "%s: %f (%f)" % (nome, cv_results.mean(), cv_results.std()) #Iprimir em um arquivo
                        print(msg)
                    '''

                    rfc = RandomForestClassifier(random_state=12)

                    from sklearn.model_selection import GridSearchCV

                    param_grid = [{"criterion": ['gini', 'entropy'],"n_estimators": [10,25,30,35,40,45,50,100],
                                   #"max_depth": [2,3,4,5,6,7],
                                  "class_weight": ["balanced",None],
                                  "min_samples_split": [2, 5, 10]}]

                    score = 'f1'

                    print("# Tunando hiperparâmetros para %s" % score)
                    print()

                    grid = GridSearchCV(rfc, param_grid, cv=2, scoring='%s_macro' % score)
                    
                    try:

                        grid = GridSearchCV(rfc, param_grid, cv=5, scoring='%s_macro' % score)
                        grid.fit(X_train, y_train)
                        
                    except ValueError:
                        
                        try:

                            grid = GridSearchCV(rfc, param_grid, cv=3, scoring='%s_macro' % score)
                            grid.fit(X_train, y_train)

                        except ValueError:

                            grid = GridSearchCV(rfc, param_grid, cv=2, scoring='%s_macro' % score)
                            grid.fit(X_train, y_train)


                    print("Melhor conjunto de hiperparâmetros encontrado:")
                    print()
                    print(grid.best_params_)
                    # print()
                    # print("Grade de valores encontrados:")
                    # print()
                    medias = grid.cv_results_['mean_test_score']
                    desvios = grid.cv_results_['std_test_score']
                    # for media, desvio, params in zip(medias, desvios, grid.cv_results_['params']):
                    #     print("%0.3f (+/-%0.03f) for %r" % (media, desvio * 2, params))
                    #     print()

                    rfc = RandomForestClassifier(**grid.best_params_, random_state=500)

            #         rfc = RandomForestClassifier(parameters = grid.best_params_, random_state=12)

                    kfold = KFold(n_splits=2, random_state=seed)

                    try:

                        kfold = StratifiedKFold(n_splits=10, random_state=seed)
                        kfoldUtilizado = "skf-10"

                    except ValueError:

                        try:

                            print("Primeiro erro!")
                            kfold = KFold(n_splits=10, random_state=seed)
                            kfoldUtilizado = "kf-10"

                        except ValueError:

                            try:

                                print("Segundo erro!")
                                kfold = StratifiedKFold(n_splits=5, random_state=seed)
                                kfoldUtilizado = "skf-5"

                            except ValueError:

                                try:

                                    print("Terceiro erro!")
                                    kfold = KFold(n_splits=5, random_state=seed)
                                    kfoldUtilizado = "kf-5"
                                
                                except ValueError:

                                    try:

                                        print("Quarto erro!")
                                        kfold = KFold(n_splits=2, random_state=seed)
                                        kfoldUtilizado = "kf-2"

                                    except:
                                        print("ERRO NA VALIDAÇÃO CRUZADA!")
                                        print("kfold utilizado: {0}".format(kfoldUtilizado))
                                        exc_type, exc_obj, exc_tb = sys.exc_info()
                                        fname = os.path.split(exc_tb.tb_frame.f_code.co_filename)[1]
                                        print(exc_type, fname, exc_tb.tb_lineno)
                                        print(sys.exc_info())

                    #Isso só serve para validar o uso do conjunto de treino 
                    #Não influencia no resultado final
        #             try:
        #                 cv_results2 = model_selection.cross_val_score(rfc, X_train, y_train, cv=kfold, scoring='f1')
        #                 msg = "%s com hiperparâmetros tunados: F1 = %f com desvio padrão = %f" % ('RFC', cv_results2.mean(), cv_results2.std())
        #                 print(msg)

        #             except:
        #                 print("ERRO NA VALIDAÇÃO CRUZADA!")
        #                 exc_type, exc_obj, exc_tb = sys.exc_info()
        #                 fname = os.path.split(exc_tb.tb_frame.f_code.co_filename)[1]
        #                 print(exc_type, fname, exc_tb.tb_lineno)
        #                 print(sys.exc_info())


                    rfc.fit(X_train, y_train) #Treinando o modelo
                    predicoes = rfc.predict(X_test) #Realizando a predição

            #         from sklearn.metrics import confusion_matrix
            #         matriz = confusion_matrix(y_test, predicoes)

            #         print(matriz)

                    from sklearn.metrics import classification_report
                    from sklearn.metrics import precision_recall_fscore_support

                    # print(classification_report(y_test, predicoes))
            #         prec, rec, fbeta, supp = precision_recall_fscore_support(y_test, predicoes, average=None)
            #         print ('precision: %.5f' %(prec[1]))
            #         print ('recall: %.5f' %(rec[1]))
            #         print ('f1: %.5f' %(fbeta[1]))
            #         print ('non-matches: %d - matches: %d' %(supp[0], supp[1]))
            #         print('')

                    # from sklearn.externals.six import StringIO  
                    # from IPython.display import Image  
                    # from sklearn.tree import export_graphviz
                    # import pydotplus
                    # dot_data = StringIO()
                    # export_graphviz(rfc, out_file=dot_data,  
                    #                 filled=True, rounded=True,
                    #                 special_characters=True, feature_names=X.columns)
                    # graph = pydotplus.graph_from_dot_data(dot_data.getvalue())  
                    # Image(graph.create_png())

                    predicoes = rfc.predict(XtoClass)

                    from sklearn.metrics import confusion_matrix
                    matriz = confusion_matrix(ytoClass, predicoes)
                    print(matriz)

                    this_tn, this_fp, this_fn, this_tp = 0, 0, 0, 0

                    this_tn, this_fp, this_fn, this_tp = confusion_matrix(ytoClass, predicoes, labels=[0,1]).ravel()
                    print('tn, fp, fn, tp')
                    print(this_tn, this_fp, this_fn, this_tp)



                    from sklearn.metrics import classification_report
                    from sklearn.metrics import precision_recall_fscore_support

                    # print(classification_report(y_test, predicoes))
            #         prec, rec, fbeta, supp = precision_recall_fscore_support(ytoClass, predicoes, average=None)
            #         print ('precision: %.5f' %(prec[1]))
            #         print ('recall: %.5f' %(rec[1]))
            #         print ('f1: %.5f' %(fbeta[1]))
            #         print ('non-matches: %d - matches: %d' %(supp[0], supp[1]))
            #         print('')


                    ########################

                    #Atualizar as estatísticas
                    abordagem = 'DS'
                    #print 'abordagem é %s' %(abordagem)

                    #algUtl = linhaAtual['algoritmosUtilizados'].item()
                    iteracao = 2
                    inspecoesManuais = linhaAtual['inspecoesManuais'].item()
                    da = linhaAtual['da'].item() + (this_tp + this_fp) #Adiciona todos os casos positivos identificados
                    dm = linhaAtual['dm'].item()             #na predição
                    ndm = linhaAtual['ndm'].item()


                    fn = float(linhaAtual['fn'].item() - this_tp ) #Não tenho certeza se é isso
                    tp = this_tp + float(linhaAtual['tp'].item()) #+ dm) #Recuperar de toClass
#                     print('tp é igual a: %d' %(tp))

                    fp = this_fp + float(linhaAtual['fp'].item())
                    #tn = tn + float(linhaAtual['tn'].item() - tp) #+ ndm) #Recuperar de toClass
                    tn = (9762 * 9763) / 2 -(tp+fp+fn)



                    precision = tp/(tp+fp)
                    recall = tp/(tp+fn)
                    fmeasure = 2*((precision*recall)/(precision+recall))

                    #Adicionando valor à última linha
            #         estatisticas.loc[(etapa, permutacao), ['abordagem', 'algoritmosUtilizados', 'iteracao', 'inspecoesManuais',
            #            'precision', 'recall', 'f-measure', 'da', 'dm', 'ndm', 'tp',
            #            'fp', 'tn', 'fn'] ] = ([abordagem, algUtl, iteracao, inspecoesManuais,
            #            precision, recall, fmeasure, da, dm, ndm, tp, fp, tn, fn])
                    estatisticas.loc[(algUtl, permutacao, etapa), ['abordagem', 'iteracao', 'inspecoesManuais',
                        'precision', 'recall', 'f-measure', 'da', 'dm', 'ndm', 'tp',
                        'fp', 'tn', 'fn'] ] = ([abordagem, iteracao, inspecoesManuais,
                        precision, recall, fmeasure, da, dm, ndm, tp, fp, tn, fn])

                    #'''

            # estatisticas = estatisticas.reset_index(level=['etapa', 'permutacao'])
            estatisticas = estatisticas.reset_index(level=['algoritmosUtilizados', 'permutacao', 'etapa'])
            # estatisticas.head()                   
            #                    

            estatisticas = estatisticas[['abordagem', 'etapa', 'algoritmosUtilizados', 'permutacao', 'iteracao', 'inspecoesManuais', 'precision', 'recall', 'f-measure', 'da', 'dm', 'ndm', 'tp', 'fp', 'tn', 'fn']]

            estatisticas[['algoritmosUtilizados', 'iteracao', 'inspecoesManuais', 'da', 'dm', 'ndm', 'tp', 'fp', 'tn', 'fn']] = \
            estatisticas[['algoritmosUtilizados', 'iteracao', 'inspecoesManuais', 'da', 'dm', 'ndm', 'tp', 'fp', 'tn', 'fn']].astype(int)

#             dirEst = "../csv/"
            # dirEst = "c:/Users/Diego/Documents/NetBeansProjects/Master-SKYAM/AS/src/csv/"
            # dirEst = "../arqResult/csv/"
        
            if(k == "ptChr"): #Se Peter Christen
                estatisticas.to_csv(dirEstat+'estatisticaDS3-PtChr.csv', sep=';', index=False)        
            elif(k == "dgArj"): #Se Diego Araújo
                estatisticas.to_csv(dirEstat+'estatisticaDS3-DgArj.csv', sep=';', index=False) 
            else: #Se Random
                estatisticas.to_csv(dirEstat+'estatisticaDS3-Random.csv', sep=';', index=False)        

            ####################### 
            #ATENÇÃO, DIEGO!#
            #Adicionar outro classificador aqui
            
#             print('lista aqui:')
#             print(lista)
            
#         for k in abordagens:
            
#             abordagemAA = ""
            
#             dirOrig = ""
#             dirEstat = ""
#             estat = ""
            
#             if(k == "ptChr"): #Se Peter Christen
                
#                 abordagemAA = '2 - AA[pet-chr]'
            
#                 dirOrig = "../csv/conjuntosDS/treinoTeste/"+base+"/"+qp+"/"+"PtChr/"
#                 dirEstat = "../csv/estatisticas/"+base+"/"+qp+"/"
#                 estat = dirEstat+"estatisticaDS2-PtChr.csv"
#     #   
#             elif(k == "dgArj"): #Se Diego Araújo
            
#                 abordagemAA = '2 - AA[dg-arj]'
            
#                 dirOrig = "../csv/conjuntosDS/treinoTeste/"+base+"/"+qp+"/"+"DgArj/"
#                 dirEstat = "../csv/estatisticas/"+base+"/"+qp+"/"
#                 estat = dirEstat+"estatisticaDS2-DgArj.csv"
                
#             elif(k == "rand"): #Se Random
            
#                 abordagemAA = '2 - AA[random]'
            
#                 dirOrig = "../csv/conjuntosDS/treinoTeste/"+base+"/"+qp+"/"+"Random/"
#                 dirEstat = "../csv/estatisticas/"+base+"/"+qp+"/"
#                 estat = dirEstat+"estatisticaDS2-Random.csv"
                
            
            print("**************************")
            print("Base: {0} - {1} - Abordagem: {2} - - Classificador: svm".format(base,qp, abordagemAA))
            print("**************************")
            
            print(dirOrig)

#             etapa = '3 - clasf'

            # estatisticas = pd.read_csv(estat, index_col=['etapa','permutacao'], sep=';')
            estatisticas = pd.read_csv(estat, index_col=['algoritmosUtilizados','permutacao','etapa'], sep=';')
        #     estatisticas.tail()

            arquivos = os.listdir(dirOrig)
            # print(arquivos)
            #print(len(arquivos))

            train = []
            test = []

            for arq in arquivos:
                if arq.startswith("train"):
                    train.append(arq)
                elif arq.startswith("test"):
                    test.append(arq)

            # print('tamanho de train: %d' %(len(train)))        

            # print('tamanho de test: %d' %(len(test)))

            # print (train)    
            # print (test)    


            #Desnecessário - Já setado acima
            #lista = ['10', '15', '20', '25'] #Assumindo que serão esses os conjuntos de algoritmos
            #ATENÇÃO, DIEGO!! ISSO MUDA PARA QP2 E QP3
#             if (qps == "qp1"):
#                 lista = ['5', '15', '25'] #Assumindo que serão esses os conjuntos de algoritmos 
#             elif (qps "qp2b"):
#                 lista == ['5'] #Assumindo que serão esses os conjuntos de algoritmos 
#             elif (qps "qp2m"):
#                 lista == ['8'] #Assumindo que serão esses os conjuntos de algoritmos 
#             elif (qps "qp2r"):
#                 lista == ['4'] #Assumindo que serão esses os conjuntos de algoritmos 
#             elif (qps "qp3all"):
#                 lista == ['8'] #Assumindo que serão esses os conjuntos de algoritmos 
#             elif (qps "qp3lot"):
#                 lista == ['5'] #Assumindo que serão esses os conjuntos de algoritmos 

            for i in lista: 

                cont = 0

                trainAtual = []
                testAtual = []

                for arq in train:
                    if '('+i+')' in arq:
        #             if 'train(10)22' in arq:    
                        trainAtual.append(arq)
                for arq in test:
                    if '('+i+')' in arq:
        #             if 'test(10)22' in arq:
                        testAtual.append(arq)

            #     print('lista desordenada')
            #     print(trainAtual)

            #     print('tamanho antes: %d' %(len(trainAtual)))

                #Ordenando a lista
                trainAtual = sorted(trainAtual)
                testAtual = sorted(testAtual)

            #     for x in trainAtual:
            #         print(x)



            # #     print('lista ordenada')
            # #     print(trainAtual)

            #     print('tamanho depois: %d' %(len(trainAtual)))

            #     print(type(trainAtual))


                print (i)

            #     print(trainAtual)
            #     print(testAtual)

                tam = len(trainAtual) #Mesma coisa para testAtual

                for pos in range(tam):
            #         print(pos)
                    print('')
                    print('##########################')
                    print('Arquivos atuais: %s e %s' %(trainAtual[pos], testAtual[pos]))
                    print('##########################')

                    treino = dirOrig+trainAtual[pos]
                    teste = dirOrig+testAtual[pos]

            #         print('treino: %s' %(treino))

            #         tp, fp, tn, fn = 0

                    num = trainAtual[pos].replace('train('+i+')','')
                    num = num.replace('.csv','')

                    cont += 1

                    print('Iteração: %d' %(cont))

            #         print('num: %s' %(num))

                    algUtl = re.sub('train.*\(', r'', trainAtual[pos]) #Alterar para fazer a substituição de tudo em uma linha só
                    algUtl = re.sub('\).*', r'', algUtl) #Alterar para fazer a substituição de tudo em uma linha só
                    algUtl = int(algUtl)


                    print('algUtl: %d' %(algUtl))

                    permutacao = int(num)
            #         linhaAtual = estatisticas.loc[('2 - AA[pet-chr]', permutacao), : ] #Armazena a linha correspondente à permutação
            #         linhaAtual = estatisticas.loc[('1 - acm diverg', permutacao), : ] #Armazena a linha correspondente à permutação
                    linhaAtual = estatisticas.loc[algUtl, permutacao, abordagemAA, : ] #Armazena a linha correspondente à permutação
        #             print (linhaAtual)
        #             print(linhaAtual.columns)

                #'''
            #         all = pd.read_csv("train.csv", index_col=False, sep=';', names=('title', 'artist', 'track01', 'track02', 'track03', 'duplicata'), header = None)
            #         toClass = pd.read_csv("test.csv", index_col=False, sep=';', names=('title', 'artist', 'track01', 'track02', 'track03', 'duplicata'), header = None)

            #         all = pd.read_csv(treino, index_col=False, sep=';', names=('title', 'artist', 'track01', 'track02', 'track03', 'duplicata'), header = None)
            #         toClass = pd.read_csv(teste, index_col=False, sep=';', names=('title', 'artist', 'track01', 'track02', 'track03', 'duplicata'), header = None)

                    all = pd.read_csv(treino, index_col=False, sep=';', names=('title', 'artist', 'track01', 'track02', 'track03', 'track10', 'track11', 'duplicata'), header = 0) #Era header = None
                    toClass = pd.read_csv(teste, index_col=False, sep=';', names=('title', 'artist', 'track01', 'track02', 'track03', 'track10', 'track11', 'duplicata'), header = 0) #Era header = None


                    # all['artist-title'] = all['artist'] * all['title']
                    # cols = list(all.columns.values)
                    # cols.pop(cols.index('duplicata'))
                    # all = all[cols+['duplicata']]

                    #Pesos baseados no Alg17

                    all['artist-title'] = all['artist'] * all['title']
                    all['soma-pesos'] = (all['artist']*1 + all['title']*2 + all['track01']*0.8 + all['track02']*0.8)/4.6
                    cols = list(all.columns.values)
                    cols.pop(cols.index('duplicata'))
                    all = all[cols+['duplicata']]

                    # toClass['artist-title'] = toClass['artist'] * toClass['title']
                    # cols = list(toClass.columns.values)
                    # cols.pop(cols.index('duplicata'))
                    # toClass = toClass[cols+['duplicata']]

                    #Pesos baseados no Alg17

                    toClass['artist-title'] = toClass['artist'] * toClass['title']
                    toClass['soma-pesos'] = (toClass['artist']*1 + toClass['title']*2 + toClass['track01']*0.8 + toClass['track02']*0.8)/4.6
                    cols = list(toClass.columns.values)
                    cols.pop(cols.index('duplicata'))
                    toClass = toClass[cols+['duplicata']]

                    #Separação do conjunto X do conjunto y
                    # X = all.loc[:,'title':'artist-title']
                    X = all.loc[:,'title':'soma-pesos']
                    y = all.duplicata

                    # XtoClass = toClass.loc[:,'title':'artist-title']
                    XtoClass = toClass.loc[:,'title':'soma-pesos']
                    ytoClass = toClass.duplicata

                    from sklearn import model_selection

                    X_train, X_test, y_train, y_test = model_selection.train_test_split(X, y, test_size=0.20, random_state=2)

                    from sklearn.svm import SVC
                    from sklearn.model_selection import StratifiedKFold
                    from sklearn.model_selection import KFold
                    from sklearn import model_selection

                    seed = 500

                    '''

                    from sklearn.linear_model import LogisticRegression
                    from sklearn.tree import DecisionTreeClassifier
                    from sklearn.neighbors import SVC
                    from sklearn.svm import SVC

                    modelos = []
                    modelos.append(('LR', LogisticRegression()))
                    modelos.append(('KNN', SVC()))
                    modelos.append(('RFC', DecisionTreeClassifier()))
                    modelos.append(('SVM', SVC()))
                    modelos.append(('RF', RandomForestClassifier()))



                    # Avaliação de cada modelo por vez
                    resultados = []
                    nomes = []
                    for nome, modelo in modelos:
                        kfold = StratifiedKFold(n_splits=10, random_state=seed) #Mudar para n-fold
                        cv_results = model_selection.cross_val_score(modelo, X_train, y_train, cv=kfold, scoring='f1')
                        msg = "%s: %f (%f)" % (nome, cv_results.mean(), cv_results.std()) #Iprimir em um arquivo
                        print(msg)
                    '''

                    svm = SVC()

                    from sklearn.model_selection import GridSearchCV

                    param_grid = [{"C": [0.001, 0.1, 10, 100, 1000], "kernel": ['rbf', 'sigmoid' , 'linear'],
                                  "class_weight": ["balanced",None],
                                  "gamma": [1e-2, 1e-3, 1e-4, 1e-5]}]

                    score = 'f1'

                    print("# Tunando hiperparâmetros para %s" % score)
                    print()

                    svm = SVC()

                    try:

                        grid = GridSearchCV(svm, param_grid, cv=2, scoring='%s_macro' % score)

                        try:

                            grid = GridSearchCV(svm, param_grid, cv=5, scoring='%s_macro' % score)
                            grid.fit(X_train, y_train)

                        except ValueError:

                            try:

                                grid = GridSearchCV(svm, param_grid, cv=3, scoring='%s_macro' % score)
                                grid.fit(X_train, y_train)

                            except ValueError:

                                grid = GridSearchCV(svm, param_grid, cv=2, scoring='%s_macro' % score)
                                grid.fit(X_train, y_train)


        #                 print("Melhor conjunto de hiperparâmetros encontrado:")
        #                 print()
        #                 print(grid.best_params_)
                        # print()
                        # print("Grade de valores encontrados:")
                        # print()
        #                 medias = grid.cv_results_['mean_test_score']
        #                 desvios = grid.cv_results_['std_test_score']
                        # for media, desvio, params in zip(medias, desvios, grid.cv_results_['params']):
                        #     print("%0.3f (+/-%0.03f) for %r" % (media, desvio * 2, params))
                        #     print()

                        svm = SVC(**grid.best_params_)

                    except ValueError:

                        svm = SVC()

            #         rfc = RandomForestClassifier(parameters = grid.best_params_, random_state=12)

                    kfold = KFold(n_splits=2, random_state=seed)

                    try:

                        kfold = StratifiedKFold(n_splits=10, random_state=seed)
                        kfoldUtilizado = "skf-10"

                    except ValueError:

                        try:

                            print("Primeiro erro!")
                            kfold = KFold(n_splits=10, random_state=seed)
                            kfoldUtilizado = "kf-10"

                        except ValueError:

                            try:

                                print("Segundo erro!")
                                kfold = StratifiedKFold(n_splits=5, random_state=seed)
                                kfoldUtilizado = "skf-5"

                            except ValueError:

                                try:

                                    print("Terceiro erro!")
                                    kfold = KFold(n_splits=5, random_state=seed)
                                    kfoldUtilizado = "kf-5"
                                
                                except ValueError:

                                    try:

                                        print("Quarto erro!")
                                        kfold = KFold(n_splits=2, random_state=seed)
                                        kfoldUtilizado = "kf-2"

                                    except:
                                        print("ERRO NA VALIDAÇÃO CRUZADA!")
                                        print("kfold utilizado: {0}".format(kfoldUtilizado))
                                        exc_type, exc_obj, exc_tb = sys.exc_info()
                                        fname = os.path.split(exc_tb.tb_frame.f_code.co_filename)[1]
                                        print(exc_type, fname, exc_tb.tb_lineno)
                                        print(sys.exc_info())

                    #Isso só serve para validar o uso do conjunto de treino 
                    #Não influencia no resultado final
        #             try:
        #                 cv_results2 = model_selection.cross_val_score(rfc, X_train, y_train, cv=kfold, scoring='f1')
        #                 msg = "%s com hiperparâmetros tunados: F1 = %f com desvio padrão = %f" % ('RFC', cv_results2.mean(), cv_results2.std())
        #                 print(msg)

        #             except:
        #                 print("ERRO NA VALIDAÇÃO CRUZADA!")
        #                 exc_type, exc_obj, exc_tb = sys.exc_info()
        #                 fname = os.path.split(exc_tb.tb_frame.f_code.co_filename)[1]
        #                 print(exc_type, fname, exc_tb.tb_lineno)
        #                 print(sys.exc_info())


                    svm.fit(X_train, y_train) #Treinando o modelo
                    predicoes = svm.predict(X_test) #Realizando a predição

            #         from sklearn.metrics import confusion_matrix
            #         matriz = confusion_matrix(y_test, predicoes)

            #         print(matriz)

                    from sklearn.metrics import classification_report
                    from sklearn.metrics import precision_recall_fscore_support

                    # print(classification_report(y_test, predicoes))
            #         prec, rec, fbeta, supp = precision_recall_fscore_support(y_test, predicoes, average=None)
            #         print ('precision: %.5f' %(prec[1]))
            #         print ('recall: %.5f' %(rec[1]))
            #         print ('f1: %.5f' %(fbeta[1]))
            #         print ('non-matches: %d - matches: %d' %(supp[0], supp[1]))
            #         print('')

                    # from sklearn.externals.six import StringIO  
                    # from IPython.display import Image  
                    # from sklearn.tree import export_graphviz
                    # import pydotplus
                    # dot_data = StringIO()
                    # export_graphviz(rfc, out_file=dot_data,  
                    #                 filled=True, rounded=True,
                    #                 special_characters=True, feature_names=X.columns)
                    # graph = pydotplus.graph_from_dot_data(dot_data.getvalue())  
                    # Image(graph.create_png())

                    predicoes = svm.predict(XtoClass)

                    from sklearn.metrics import confusion_matrix
                    matriz = confusion_matrix(ytoClass, predicoes)
                    print(matriz)

                    this_tn, this_fp, this_fn, this_tp = 0, 0, 0, 0

                    this_tn, this_fp, this_fn, this_tp = confusion_matrix(ytoClass, predicoes, labels=[0,1]).ravel()
                    print('tn, fp, fn, tp')
                    print(this_tn, this_fp, this_fn, this_tp)



                    from sklearn.metrics import classification_report
                    from sklearn.metrics import precision_recall_fscore_support

                    # print(classification_report(y_test, predicoes))
            #         prec, rec, fbeta, supp = precision_recall_fscore_support(ytoClass, predicoes, average=None)
            #         print ('precision: %.5f' %(prec[1]))
            #         print ('recall: %.5f' %(rec[1]))
            #         print ('f1: %.5f' %(fbeta[1]))
            #         print ('non-matches: %d - matches: %d' %(supp[0], supp[1]))
            #         print('')


                    ########################

                    #Atualizar as estatísticas
                    abordagem = 'DS'
                    #print 'abordagem é %s' %(abordagem)

                    #algUtl = linhaAtual['algoritmosUtilizados'].item()
                    iteracao = 2
                    inspecoesManuais = linhaAtual['inspecoesManuais'].item()
                    da = linhaAtual['da'].item() + (this_tp + this_fp) #Adiciona todos os casos positivos identificados
                    dm = linhaAtual['dm'].item()             #na predição
                    ndm = linhaAtual['ndm'].item()


                    fn = float(linhaAtual['fn'].item() - this_tp ) #Não tenho certeza se é isso
                    tp = this_tp + float(linhaAtual['tp'].item()) #+ dm) #Recuperar de toClass
                    print('tp é igual a: %d' %(tp))

                    fp = this_fp + float(linhaAtual['fp'].item())
                    #tn = tn + float(linhaAtual['tn'].item() - tp) #+ ndm) #Recuperar de toClass
                    tn = (9762 * 9763) / 2 -(tp+fp+fn)



                    precision = tp/(tp+fp)
                    recall = tp/(tp+fn)
                    fmeasure = 2*((precision*recall)/(precision+recall))

                    #Adicionando valor à última linha
            #         estatisticas.loc[(etapa, permutacao), ['abordagem', 'algoritmosUtilizados', 'iteracao', 'inspecoesManuais',
            #            'precision', 'recall', 'f-measure', 'da', 'dm', 'ndm', 'tp',
            #            'fp', 'tn', 'fn'] ] = ([abordagem, algUtl, iteracao, inspecoesManuais,
            #            precision, recall, fmeasure, da, dm, ndm, tp, fp, tn, fn])
                    estatisticas.loc[(algUtl, permutacao, etapa), ['abordagem', 'iteracao', 'inspecoesManuais',
                        'precision', 'recall', 'f-measure', 'da', 'dm', 'ndm', 'tp',
                        'fp', 'tn', 'fn'] ] = ([abordagem, iteracao, inspecoesManuais,
                        precision, recall, fmeasure, da, dm, ndm, tp, fp, tn, fn])

                    #'''

            # estatisticas = estatisticas.reset_index(level=['etapa', 'permutacao'])
            estatisticas = estatisticas.reset_index(level=['algoritmosUtilizados', 'permutacao', 'etapa'])
            # estatisticas.head()                   
            #                    

            estatisticas = estatisticas[['abordagem', 'etapa', 'algoritmosUtilizados', 'permutacao', 'iteracao', 'inspecoesManuais', 'precision', 'recall', 'f-measure', 'da', 'dm', 'ndm', 'tp', 'fp', 'tn', 'fn']]

            estatisticas[['algoritmosUtilizados', 'iteracao', 'inspecoesManuais', 'da', 'dm', 'ndm', 'tp', 'fp', 'tn', 'fn']] = \
            estatisticas[['algoritmosUtilizados', 'iteracao', 'inspecoesManuais', 'da', 'dm', 'ndm', 'tp', 'fp', 'tn', 'fn']].astype(int)

        #     dirEst = "../csv/"
            # dirEst = "c:/Users/Diego/Documents/NetBeansProjects/Master-SKYAM/AS/src/csv/"
            # dirEst = "../arqResult/csv/"
            
            if(k == "ptChr"): #Se Peter Christen
                estatisticas.to_csv(dirEstat+'estatisticaDS3-PtChr-svm.csv', sep=';', index=False)        
            elif(k == "dgArj"): #Se Diego Araújo
                estatisticas.to_csv(dirEstat+'estatisticaDS3-DgArj-svm.csv', sep=';', index=False) 
            else: #Se Random
                estatisticas.to_csv(dirEstat+'estatisticaDS3-Random-svm.csv', sep=';', index=False)        

Base atual: cd
QP atual: qp3lot
**************************
Base: cd - qp3lot - Abordagem: 2 - AA[dg-arj] - Classificador: rf
**************************
../csv/conjuntosDS/treinoTeste/cd/qp3lot/DgArj-k0.01/
5

##########################
Arquivos atuais: train(5)1.csv e test(5)1.csv
##########################
Iteração: 1
algUtl: 5
# Tunando hiperparâmetros para f1

Melhor conjunto de hiperparâmetros encontrado:

{'class_weight': 'balanced', 'criterion': 'entropy', 'min_samples_split': 2, 'n_estimators': 25}
[[ 2  1]
 [ 1 20]]
tn, fp, fn, tp
2 1 1 20

##########################
Arquivos atuais: train(5)10.csv e test(5)10.csv
##########################
Iteração: 2
algUtl: 5
# Tunando hiperparâmetros para f1

Melhor conjunto de hiperparâmetros encontrado:

{'class_weight': 'balanced', 'criterion': 'gini', 'min_samples_split': 2, 'n_estimators': 10}
[[35  5]
 [ 6 46]]
tn, fp, fn, tp
35 5 6 46

##########################
Arquivos atuais: train(5)100.csv e test(5)100.csv
######################

/home/diego/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/diego/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/diego/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/diego/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/diego/anaconda3/lib/python

Melhor conjunto de hiperparâmetros encontrado:

{'class_weight': 'balanced', 'criterion': 'entropy', 'min_samples_split': 10, 'n_estimators': 25}
[[0 0]
 [1 8]]
tn, fp, fn, tp
0 0 1 8

##########################
Arquivos atuais: train(5)102.csv e test(5)102.csv
##########################
Iteração: 5
algUtl: 5
# Tunando hiperparâmetros para f1

Melhor conjunto de hiperparâmetros encontrado:

{'class_weight': None, 'criterion': 'entropy', 'min_samples_split': 2, 'n_estimators': 25}
[[16  2]
 [ 0 22]]
tn, fp, fn, tp
16 2 0 22

##########################
Arquivos atuais: train(5)103.csv e test(5)103.csv
##########################
Iteração: 6
algUtl: 5
# Tunando hiperparâmetros para f1

Melhor conjunto de hiperparâmetros encontrado:

{'class_weight': None, 'criterion': 'entropy', 'min_samples_split': 10, 'n_estimators': 45}
[[1]]
tn, fp, fn, tp
0 0 0 1

##########################
Arquivos atuais: train(5)104.csv e test(5)104.csv
##########################
Iteração: 7
algUtl: 5
# Tunando hip

/home/diego/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/diego/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/diego/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/diego/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/diego/anaconda3/lib/python

Melhor conjunto de hiperparâmetros encontrado:

{'class_weight': 'balanced', 'criterion': 'gini', 'min_samples_split': 10, 'n_estimators': 35}
[[ 2  2]
 [ 0 23]]
tn, fp, fn, tp
2 2 0 23

##########################
Arquivos atuais: train(5)105.csv e test(5)105.csv
##########################
Iteração: 8
algUtl: 5
# Tunando hiperparâmetros para f1

Melhor conjunto de hiperparâmetros encontrado:

{'class_weight': 'balanced', 'criterion': 'gini', 'min_samples_split': 5, 'n_estimators': 30}
[[2 4]
 [0 7]]
tn, fp, fn, tp
2 4 0 7

##########################
Arquivos atuais: train(5)106.csv e test(5)106.csv
##########################
Iteração: 9
algUtl: 5
# Tunando hiperparâmetros para f1

Melhor conjunto de hiperparâmetros encontrado:

{'class_weight': 'balanced', 'criterion': 'entropy', 'min_samples_split': 2, 'n_estimators': 10}
[[ 7  2]
 [ 1 22]]
tn, fp, fn, tp
7 2 1 22

##########################
Arquivos atuais: train(5)107.csv e test(5)107.csv
##########################
Iteração: 10
algU

...

/home/diego/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/diego/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/diego/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/diego/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/diego/anaconda3/lib/python

[[1]]
tn, fp, fn, tp
1 0 0 0
tp é igual a: 254

##########################
Arquivos atuais: train(5)148.csv e test(5)148.csv
##########################
Iteração: 55
algUtl: 5
# Tunando hiperparâmetros para f1



/home/diego/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/diego/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/diego/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/diego/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/diego/anaconda3/lib/python

[[1]]
tn, fp, fn, tp
0 0 0 1
tp é igual a: 236

##########################
Arquivos atuais: train(5)149.csv e test(5)149.csv
##########################
Iteração: 56
algUtl: 5
# Tunando hiperparâmetros para f1



/home/diego/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/diego/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/diego/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/diego/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/diego/anaconda3/lib/python